In [1]:
import os, pandas as pd, json
from collections import OrderedDict

In [2]:
import re

In [3]:
routesFolder = 'route jsons'
outputFolder = 'data cleaning/'

In [4]:
combiner = []

In [ ]:
for root, subdirs, files in os.walk(routesFolder):
    print(root)
    files = [x for x in files if x.endswith('.json')]
    print(files)
    
    for file in files:
        row = OrderedDict({ 'folder': root })
        row['jsonFile'] = file
        
        data = json.load(open(os.path.join(root,file),'r'))
        row.update(data)
        combiner.append(row.copy())
    

route jsons
[]
route jsons/26.11.18
[]
route jsons/26.11.18/BKP - Santosh
['113M.json', '113M_216.json', '115.json', '116N.json', '116P.json', '127K.json', '127KKL.json', '131_I_M.json', '216.json', '216LG.json', '216MG.json', '216T.json', '217A.json', '218L.json', '222.json', '9X.json']
route jsons/26.11.18/DSNR - Surya
['156L_216DLF.json', '156_216D_LF_.json', '205F_218D.json', '218D_CS.json', '218D_LF.json', '218D_LF_DSNPTC_.json', '218D_LF_LB_.json', '218D_MD.json', '218_LF_CBSPTC_.json', '300D.json', '300D_126.json', '300L.json', '300L_126.json', '90L_MD.json']
route jsons/26.11.18/KCG - Nikhil
['1.json', '102_540.json', '115.json', '116N.json', '127N.json', '127T.json', '136H.json', '136N.json', '1B.json', '1J.json', '1P.json', '216.json', '280.json', '2j.json', '3K.json', '3n.json', '471P.json', '540M.json', '83F.json']
route jsons/26.11.18/MSRD1 - Vishal
['113M.json', '113YK.json', '115.json', '115M.json', '137.json', '190R.json', '1Z.json', '218_MSRD.json', '219.json', '3HN.js

route jsons/4.12.18/KGD - Shishir Akkshath
['242PG.json', '117.json', '15H.json', '15H_15D.json', '15H_20.json', '15H_242RG.json', '16A.json', '16AK.json', '16C.json', '17CS.json', '17D.json', '17H.json', '17HN.json', '17H_219.json', '17JJ.json', '17S.json', '217.json', '218.json', '241T.json', '242.json', '242A.json', '242B.json', '242G.json', '242RG.json', '24S.json', '24S_219L.json', '281.json', '290F.json', '37.json', '3D.json', '3H.json', '3HN.json', '3K.json', '3K_252.json', '3M.json', '3Y.json', '496.json', '497.json', '546.json', '571.json', '572.json', '572M.json', '573.json', '577.json', '578.json', '579.json', '580.json', '6HN.json', '6H_288.json', '6LG.json']
route jsons/4.12.18/MDCL - Nikhil
['212_702.json', '219_229.json', '227.json', '229.json', '495.json', '567C.json', '585.json', '586.json', '587.json', '588.json', '589.json', '590.json', '591.json', '90L_229.json']
route jsons/5.12.18
[]
route jsons/5.12.18/HCU - akkshath
['194V.json', '10HA.json', '10HK.json', '10H_U

In [ ]:
df = pd.DataFrame(combiner)
df

In [ ]:
df.to_csv(outputFolder + 'jsons2csv.csv')

In [ ]:
len(df)

## ok, now let's wring out the stops from here to a CSV such that we can trace them back.

In [ ]:
def nameClean(x):
    
    # find+replace, ignore case. From https://stackoverflow.com/a/919074/4355695
    pattern1 = re.compile("bustop", re.IGNORECASE)
    pattern2 = re.compile("busstop", re.IGNORECASE)
    pattern3 = re.compile("bus stop", re.IGNORECASE)
    
    cleaned = pattern1.sub("", x)
    cleaned = pattern2.sub("", cleaned)
    cleaned = pattern3.sub("", cleaned)
    
    # remove leading, trailing spaces and newlines
    cleaned = cleaned.strip()
    
    if cleaned != x:
        print('"{}" cleaned to: "{}"'.format(x,cleaned))
    
    return cleaned

#test:
nameClean('Koti Bus Stop')

In [ ]:
stopsCollector = []
for n,routeRow in df.iterrows():
    
    # get all metadata to tie the stop back to its original place in the route json.
    row = OrderedDict({
        'folder': routeRow['folder'],
        'jsonFile': routeRow['jsonFile'],
        'routeName': routeRow['routeName']
    })
    print('\nProcessing {}/{}'.format(row['folder'],row['jsonFile']))
    
    count = 0
    for n,stop in enumerate(routeRow['stops0'].split('\n')):
        row['direction_id'] = 0
        # row['stop_sequence'] = n+1
        row['stop_name'] = nameClean(stop)
        if row['stop_name'] != '':
            count += 1
            row['stop_sequence'] = count
            stopsCollector.append(row.copy())
    
    count = 0
    for n,stop in enumerate(routeRow['stops1'].split('\n')):
        row['direction_id'] = 1
        # row['stop_sequence'] = n+1
        row['stop_name'] = nameClean(stop)
        if row['stop_name'] != '':
            count += 1
            row['stop_sequence'] = count
            stopsCollector.append(row.copy())
    

In [ ]:
stopsDf = pd.DataFrame(stopsCollector)
stopsDf

In [ ]:
stopsDf.to_csv(outputFolder + 'stopsList-orig.csv',index_label='sr')

In [ ]:
stopsDf['stop_name_dataclean'] = stopsDf['stop_name']

In [ ]:
stopsDf.to_csv(outputFolder + 'stopsList-dataclean.csv',index_label='sr')

In [ ]:
len(stopsDf)